In [14]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

#if __name__ == "__main__":
#  tf.app.run()


In [15]:
def cnn_model_fn(features, labels, mode):
    input_layer = tf.reshape(features ['x'],[-1,28,28,1])
    
    #Convolution Layer #1
    conv1 = tf.layers.conv2d(inputs = input_layer,filters = 32,
                            kernel_size =[5,5],padding = 'same',
                            activation = tf.nn.relu)
    #Pooling Layer #1
    pool1 = tf.layers.max_pooling2d(inputs = conv1, pool_size = [2,2], strides =2)
    
    #Convolution Layer #2
    conv2 = tf.layers.conv2d(inputs=pool1, filters = 64,
                kernel_size=[5, 5], padding = "same", 
                activation=tf.nn.relu)
    
    #Pooling Layer #2
    pool2 = tf.layers.max_pooling2d(inputs = conv2, pool_size = [2, 2], strides = 2)
    
    #Dense Layer
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
    dense = tf.layers.dense(inputs = pool2_flat, units = 1024, activation = tf.nn.relu)
    dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training = mode == tf.estimator.ModeKeys.TRAIN)
    
    #Logits layers
    
    logits = tf.layers.dense(inputs = dropout, units = 10)
    
    
    predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
      }
        
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

    # Calculate Loss (for both TRAIN and EVAL modes)
    loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)
    
    
  # Configure the Training Op (for TRAIN mode)
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)


# Add evaluation metrics (for EVAL mode)
    eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)







In [16]:
# Load training and eval data
mnist = tf.contrib.learn.datasets.load_dataset("mnist")
train_data = mnist.train.images # Returns np.array
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
eval_data = mnist.test.images # Returns np.array
eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)


Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz


In [17]:
mnist_classifier = tf.estimator.Estimator(
    model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")


INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_task_type': 'worker', '_log_step_count_steps': 100, '_is_chief': True, '_tf_random_seed': None, '_save_checkpoints_secs': 600, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f2e48d0e438>, '_task_id': 0, '_session_config': None, '_model_dir': '/tmp/mnist_convnet_model', '_keep_checkpoint_every_n_hours': 10000, '_num_worker_replicas': 1, '_save_summary_steps': 100, '_service': None, '_num_ps_replicas': 0, '_master': '', '_save_checkpoints_steps': None, '_keep_checkpoint_max': 5}


In [18]:
# Set up logging for predictions
tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)


In [19]:
train_input_fn = tf.estimator.inputs.numpy_input_fn(
    x={"x": train_data},
    y=train_labels,
    batch_size=100,
    num_epochs=None,
    shuffle=True)
mnist_classifier.train(
    input_fn=train_input_fn,
    steps=20000,
    hooks=[logging_hook])


INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:probabilities = [[0.1117494  0.08566111 0.09722468 0.09385237 0.09662856 0.10111809
  0.10625219 0.0873552  0.10662875 0.11352967]
 [0.11846295 0.09081044 0.10588893 0.08834385 0.11075414 0.10152936
  0.09611507 0.08698798 0.10076026 0.10034699]
 [0.10559606 0.08469483 0.10331986 0.09739365 0.09081832 0.10666608
  0.09794133 0.10561789 0.10467146 0.10328051]
 [0.11536577 0.08766039 0.10805956 0.09241699 0.09966639 0.0959608
  0.100839   0.08922152 0.11617351 0.09463609]
 [0.11342973 0.09214886 0.09850498 0.10467787 0.09860016 0.10220753
  0.09822016 0.08855676 0.10507136 0.09858255]
 [0.1167196  0.08530084 0.09490439 0.08664119 0.09696599 0.1055324
  0.09680723 0.09504923 0.10593016 0.11614899]
 [0.1058801  0.09071261 0.10517441 0.09167713 0.10105669 0.10318729
  0.09682465 0.09429143 0.10759125 0.10360444]
 [0.12266737 0.08234852 0.08919782 0.0

INFO:tensorflow:loss = 2.302937, step = 1
INFO:tensorflow:probabilities = [[0.11079875 0.09297794 0.10602319 0.09045279 0.10774773 0.09733323
  0.09314487 0.09127614 0.10607079 0.1041746 ]
 [0.10711323 0.0954575  0.10798931 0.09431245 0.09762207 0.10251953
  0.0977613  0.09519704 0.10051292 0.10151463]
 [0.111885   0.09511486 0.09463575 0.09122364 0.08839263 0.10653426
  0.09830795 0.08723969 0.12166538 0.10500074]
 [0.12478355 0.08473684 0.10815981 0.08994742 0.09119878 0.10839991
  0.09214983 0.0824351  0.11064281 0.10754598]
 [0.12054685 0.09967264 0.08887435 0.09484798 0.09928938 0.10411479
  0.09733726 0.09023917 0.10213967 0.1029379 ]
 [0.11470445 0.0824463  0.10984627 0.08904798 0.09706783 0.11221211
  0.10280195 0.09257289 0.10322347 0.0960767 ]
 [0.10657859 0.09105901 0.10056619 0.09119643 0.09472835 0.09712593
  0.09865356 0.10626958 0.10163157 0.11219084]
 [0.11668509 0.09585275 0.09302595 0.0904479  0.0988381  0.09625459
  0.09626197 0.09721684 0.11177896 0.10363781]
 [0.12

INFO:tensorflow:global_step/sec: 5.49895
INFO:tensorflow:probabilities = [[0.09747526 0.09503577 0.10966052 0.09258632 0.10986944 0.10191185
  0.10339084 0.09059574 0.1017918  0.0976825 ]
 [0.10504842 0.09469419 0.10079157 0.09502324 0.09780269 0.10698633
  0.09911737 0.09266399 0.10601605 0.10185614]
 [0.1032109  0.08440717 0.10487426 0.09278078 0.09896982 0.11165614
  0.10111002 0.10175905 0.09961905 0.10161275]
 [0.11949429 0.08433865 0.09631445 0.09424675 0.09856473 0.10558594
  0.10755073 0.09168947 0.09627003 0.10594492]
 [0.13686505 0.08729249 0.08685093 0.09409819 0.09859824 0.10146868
  0.1037589  0.09122226 0.10394664 0.09589863]
 [0.10324977 0.09165215 0.10086425 0.097317   0.10171625 0.10328639
  0.09209593 0.10208697 0.09824672 0.10948455]
 [0.11449689 0.08168457 0.10568985 0.08775255 0.09771959 0.11368236
  0.09713463 0.08386569 0.10670266 0.1112712 ]
 [0.11243924 0.08272578 0.1027563  0.1070896  0.10194898 0.09476644
  0.09079253 0.09715626 0.1061722  0.10415267]
 [0.103

INFO:tensorflow:loss = 2.283308, step = 101 (18.188 sec)
INFO:tensorflow:probabilities = [[0.10112594 0.09440908 0.09465238 0.1040267  0.10142676 0.10153344
  0.0974937  0.09289466 0.10428626 0.10815099]
 [0.10662531 0.09267752 0.10040034 0.09973849 0.10221284 0.09993099
  0.10311372 0.08866664 0.10650501 0.10012921]
 [0.12056963 0.08025078 0.1024975  0.09853026 0.09744213 0.10986869
  0.10855711 0.10361939 0.09360479 0.08505974]
 [0.11028882 0.07345629 0.11400534 0.0918473  0.0873376  0.10022086
  0.10464951 0.08579705 0.11520718 0.11718997]
 [0.12157668 0.0837067  0.10630568 0.09426597 0.08967439 0.11447933
  0.10196809 0.0865509  0.10424528 0.09722695]
 [0.11476129 0.0933145  0.09413684 0.10036168 0.10561121 0.08702934
  0.09219951 0.09928866 0.1039305  0.10936649]
 [0.1011256  0.09163786 0.09590965 0.09241564 0.10871406 0.10724135
  0.0962444  0.1007317  0.10285954 0.10312024]
 [0.1180648  0.09004243 0.11998565 0.09565578 0.09310167 0.09514879
  0.10714543 0.08584189 0.1017895  0.0

INFO:tensorflow:global_step/sec: 5.16578
INFO:tensorflow:probabilities = [[0.10556357 0.08642066 0.10423002 0.09561898 0.1042443  0.10970413
  0.10715154 0.08516356 0.10125872 0.10064445]
 [0.10233613 0.08921617 0.10844637 0.09308644 0.09828297 0.09445143
  0.11437694 0.09517771 0.10422742 0.10039844]
 [0.10155614 0.09918524 0.101243   0.09382012 0.09369151 0.10415598
  0.09478047 0.09574215 0.10182144 0.1140039 ]
 [0.1059007  0.08462152 0.09370822 0.09325451 0.08721185 0.09540624
  0.10249931 0.10192086 0.11256451 0.12291228]
 [0.11175325 0.08684935 0.1026762  0.09217058 0.10248077 0.10404753
  0.11507449 0.0954945  0.10153493 0.08791839]
 [0.10407014 0.09600193 0.08644179 0.09905192 0.09506959 0.11045636
  0.10271916 0.09127244 0.11185206 0.10306466]
 [0.10688866 0.09022387 0.09939036 0.09787551 0.09162205 0.09611566
  0.0979123  0.10192859 0.10835239 0.10969055]
 [0.12630503 0.08201457 0.09706181 0.09335863 0.0910083  0.0997062
  0.12915576 0.0917173  0.10031238 0.08936008]
 [0.1069

...

INFO:tensorflow:global_step/sec: 5.71874
INFO:tensorflow:probabilities = [[0.9994642  0.00000154 0.00036128 0.00001147 0.00000032 0.00009596
  0.0000324  0.00001592 0.0000063  0.00001067]
 [0.00000622 0.9176487  0.00074221 0.01093961 0.02066363 0.00480163
  0.01115665 0.00020155 0.03267827 0.00116152]
 [0.00000024 0.0000043  0.00000423 0.00009417 0.97317547 0.00006844
  0.00000346 0.00006193 0.00033908 0.02624866]
 [0.90949106 0.00000099 0.00177558 0.00000513 0.00000806 0.0672889
  0.01625326 0.00000014 0.00514914 0.00002775]
 [0.00000573 0.9952826  0.00025671 0.00056369 0.00027871 0.00020209
  0.00039333 0.0000093  0.00299367 0.0000143 ]
 [0.00000103 0.00331246 0.96612984 0.0292493  0.00000019 0.00117649
  0.00011274 0.00000079 0.000017   0.00000003]
 [0.00000001 0.00000472 0.9997342  0.00024373 0.         0.00000001
  0.         0.00000294 0.00001442 0.        ]
 [0.00001188 0.00000645 0.00000442 0.00060444 0.00000698 0.00037462
  0.         0.52744067 0.00018573 0.4713649 ]
 [0.0005

INFO:tensorflow:loss = 0.16351505, step = 19801 (17.480 sec)
INFO:tensorflow:probabilities = [[0.00036944 0.00000002 0.00000879 0.00012523 0.00042297 0.00002494
  0.00000485 0.32520413 0.00053612 0.67330354]
 [0.00004316 0.00000196 0.00002813 0.00007123 0.00000001 0.997719
  0.00000164 0.00000033 0.00213092 0.00000367]
 [0.00257361 0.02891106 0.00150832 0.04865845 0.0054618  0.8360681
  0.04546019 0.00128772 0.01000291 0.02006792]
 [0.00000808 0.9993205  0.00018393 0.00012997 0.00004704 0.00000711
  0.00006603 0.00002262 0.00021172 0.0000029 ]
 [0.00028094 0.00020304 0.00037435 0.00017739 0.00158894 0.00054707
  0.9924975  0.00002531 0.00428233 0.00002314]
 [0.9960777  0.00002842 0.00231261 0.00022914 0.00003653 0.0004364
  0.00070312 0.00004208 0.0000613  0.00007261]
 [0.00098224 0.02036795 0.00208358 0.00153231 0.00064337 0.00904356
  0.00189535 0.00079942 0.95316434 0.00948793]
 [0.00000219 0.00000406 0.0000123  0.00116506 0.00436953 0.00003885
  0.00000002 0.00108056 0.00058465 0.9

INFO:tensorflow:Saving checkpoints for 19881 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:global_step/sec: 5.69642
INFO:tensorflow:probabilities = [[0.5495423  0.00082408 0.29779026 0.01979009 0.00032436 0.03733226
  0.0008265  0.00650555 0.0070148  0.08004981]
 [0.99948704 0.00000052 0.00014516 0.00000314 0.00013634 0.00000446
  0.00001072 0.00001451 0.00000037 0.00019781]
 [0.         0.         0.00003093 0.9998273  0.         0.00000016
  0.         0.00000654 0.00009062 0.00004457]
 [0.00161641 0.00157475 0.00063327 0.00019441 0.00162129 0.00317663
  0.9896526  0.00000717 0.00148645 0.00003697]
 [0.42221996 0.00043393 0.01747493 0.00000791 0.51173    0.00204868
  0.03146402 0.0007309  0.00020009 0.01368957]
 [0.0000037  0.00000059 0.00023163 0.00111545 0.00000615 0.00012307
  0.00000156 0.00000003 0.99849236 0.00002543]
 [0.00000007 0.00000057 0.00000008 0.00000352 0.99283856 0.00002153
  0.00000017 0.00005908 0.00004768 0.00702868]
 [0.00021466 0.00005617 0.91480845 

INFO:tensorflow:loss = 0.09167314, step = 19901 (17.555 sec)
INFO:tensorflow:probabilities = [[0.0000107  0.00173082 0.00055683 0.00011516 0.9793428  0.00002164
  0.00030922 0.00036235 0.00019731 0.01735307]
 [0.00000015 0.00005876 0.00001224 0.9993672  0.00000008 0.00009661
  0.00000006 0.00000004 0.00044565 0.00001937]
 [0.00000006 0.00002057 0.00003152 0.0000283  0.99518436 0.00000181
  0.00000942 0.00002817 0.00004098 0.00465475]
 [0.00059464 0.00000223 0.00004804 0.00010701 0.00863045 0.983123
  0.00701673 0.00003046 0.00023242 0.00021499]
 [0.00004495 0.00000494 0.98598075 0.01292489 0.00014553 0.00000866
  0.00001417 0.00007142 0.00012221 0.00068238]
 [0.00000732 0.98656416 0.00081938 0.00169912 0.00485066 0.00052048
  0.00023039 0.00011592 0.00484945 0.00034308]
 [0.00049729 0.00000017 0.9971511  0.00172469 0.00000909 0.00000048
  0.00000005 0.00050505 0.00000689 0.00010533]
 [0.00134337 0.00000998 0.00133394 0.00005516 0.8950603  0.00024747
  0.00047851 0.00025354 0.00006525 0

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.1293624.
